# Explore 3D alignment

In [ ]:
import numpy as np
import trimesh
from typing import Optional
from shapely.geometry import Polygon
from sklearn.decomposition import PCA
from itertools import permutations
import cadquery as cq
from scipy.spatial import KDTree
import tempfile

IndentationError: unexpected indent (2594936682.py, line 8)

In [ ]:
def cq_to_trimesh(workplane: cq.Workplane) -> trimesh.Trimesh:
    """
    Converts a CadQuery Workplane object into a trimesh.Trimesh object.
    """
    with tempfile.NamedTemporaryFile(suffix=".stl", delete=False) as temp_file:
        workplane.export(temp_file.name)
        mesh = trimesh.load_mesh(temp_file.name)
    return mesh

In [ ]:
def plot_vertices(mesh):
    extent = np.max(mesh.extents)
    if extent > 1e-7:
        mesh.apply_scale(1.0 / extent)

    scene = trimesh.Scene()
    scene.add_geometry(mesh)

    print(f"# Vertices: {len(mesh.vertices)}")

    for vertex_pos in mesh.vertices:
        sphere = trimesh.creation.icosphere(radius=0.02, face_colors=[255, 0, 0, 255])
        sphere.apply_translation(vertex_pos)
        scene.add_geometry(sphere)

    return scene.show()

## Align

In [ ]:
def align_rot(
    source_mesh: trimesh.Trimesh, target_mesh: trimesh.Trimesh
) -> trimesh.Trimesh:
    # 1. Copy vertex arrays and center them
    source_vertices = source_mesh.vertices - source_mesh.centroid
    target_vertices = target_mesh.vertices - target_mesh.centroid

    # 2. Match vertex counts (for Procrustes alignment)
    n = min(len(source_vertices), len(target_vertices))

    print(len(target_vertices), len(source_vertices))
    source_vertices = source_vertices[:n]
    target_vertices = target_vertices[:n]

    # 3. Compute best-fit rotation matrix using SVD
    U, _, Vt = np.linalg.svd(target_vertices.T @ source_vertices)
    R_opt = U @ Vt

    # 4. Fix improper rotation (reflection case)
    if np.linalg.det(R_opt) < 0:
        U[:, -1] *= -1
        R_opt = U @ Vt

    # 5. Build transformation matrix
    T = np.eye(4)
    T[:3, :3] = R_opt
    T[:3, 3] = target_mesh.centroid - R_opt @ source_mesh.centroid

    # 6. Apply transformation
    aligned_mesh = source_mesh.copy()
    aligned_mesh.apply_transform(T)

    return aligned_mesh


def align_rot2(
    source_mesh: trimesh.Trimesh, target_mesh: trimesh.Trimesh
) -> trimesh.Trimesh:
    # 1. Center the vertices
    source_vertices = source_mesh.vertices - source_mesh.centroid
    target_vertices = target_mesh.vertices - target_mesh.centroid

    # 2. Match each source vertex to the nearest target vertex
    tree = KDTree(target_vertices)
    _, indices = tree.query(source_vertices)
    indices = np.asarray(indices).reshape(-1)  # 🔧 Ensure it's 1D

    matched_target_vertices = target_vertices[indices]

    # 3. Ensure proper shapes
    source_vertices = np.asarray(source_vertices)
    matched_target_vertices = np.asarray(matched_target_vertices)

    if source_vertices.ndim != 2 or source_vertices.shape[1] != 3:
        raise ValueError(f"source_vertices shape invalid: {source_vertices.shape}")
    if matched_target_vertices.ndim != 2 or matched_target_vertices.shape[1] != 3:
        raise ValueError(
            f"matched_target_vertices shape invalid: {matched_target_vertices.shape}"
        )

    # 4. Compute best-fit rotation matrix
    print(source_vertices, matched_target_vertices)

    H = source_vertices.T @ matched_target_vertices
    U, _, Vt = np.linalg.svd(H)
    R_opt = Vt.T @ U.T

    # 5. Fix improper rotation
    if np.linalg.det(R_opt) < 0:
        Vt[-1, :] *= -1
        R_opt = Vt.T @ U.T

    # 6. Build transformation matrix
    T = np.eye(4)
    T[:3, :3] = R_opt
    T[:3, 3] = target_mesh.centroid - R_opt @ source_mesh.centroid

    # 7. Apply transform
    aligned_mesh = source_mesh.copy()
    aligned_mesh.apply_transform(T)
    return aligned_mesh

In [ ]:
# import copy

# import numpy as np
# import open3d as o3d


# # def draw_registration_result(source, target, transformation):
# #     source_temp = copy.deepcopy(source)
# #     target_temp = copy.deepcopy(target)
# #     source_temp.paint_uniform_color([1, 0.706, 0])
# #     target_temp.paint_uniform_color([0, 0.651, 0.929])
# #     source_temp.transform(transformation)
# #     o3d.visualization.draw_geometries([source_temp, target_temp])


# def tri_to_o(trimesh_mesh: trimesh.Trimesh):
#     vertices = np.asarray(trimesh_mesh.vertices)
#     triangles = np.asarray(trimesh_mesh.faces)

#     o3d_mesh = o3d.geometry.TriangleMesh()
#     o3d_mesh.vertices = o3d.utility.Vector3dVector(vertices)
#     o3d_mesh.triangles = o3d.utility.Vector3iVector(triangles)

#     return o3d_mesh


# def o_to_tri(o3d_mesh):
#     vertices = np.asarray(o3d_mesh.vertices)
#     faces = np.asarray(o3d_mesh.triangles)

#     return trimesh.Trimesh(vertices=vertices, faces=faces)

# def preprocess_point_cloud(pcd, voxel_size):
#     print(":: Downsample with a voxel size %.3f." % voxel_size)
#     pcd_down = pcd.voxel_down_sample(voxel_size)

#     radius_normal = voxel_size * 2
#     print(":: Estimate normal with search radius %.3f." % radius_normal)
#     pcd_down.estimate_normals(
#         o3d.geometry.KDTreeSearchParamHybrid(radius=radius_normal, max_nn=30))

#     radius_feature = voxel_size * 5
#     print(":: Compute FPFH feature with search radius %.3f." % radius_feature)
#     pcd_fpfh = o3d.pipelines.registration.compute_fpfh_feature(
#         pcd_down,
#         o3d.geometry.KDTreeSearchParamHybrid(radius=radius_feature, max_nn=100))
#     return pcd_down, pcd_fpfh


# def execute_global_registration(source_down, target_down, source_fpfh,
#                                 target_fpfh, voxel_size):
#     distance_threshold = voxel_size * 1.5
#     result = o3d.pipelines.registration.registration_ransac_based_on_feature_matching(
#         source_down, target_down, source_fpfh, target_fpfh, True,
#         distance_threshold,
#         o3d.pipelines.registration.TransformationEstimationPointToPoint(False),
#         3, [
#             o3d.pipelines.registration.CorrespondenceCheckerBasedOnEdgeLength(
#                 0.9),
#             o3d.pipelines.registration.CorrespondenceCheckerBasedOnDistance(
#                 distance_threshold)
#         ], o3d.pipelines.registration.RANSACConvergenceCriteria(100000, 0.999))
#     return result


# def align(source_mesh,target_mesh):
#     voxel_size = 0.01
#     target = tri_to_o(target_mesh).sample_points_uniformly(1000)
#     source = tri_to_o(source_mesh).sample_points_uniformly(1000)

#     source_down, source_fpfh = preprocess_point_cloud(source, voxel_size)
#     target_down, target_fpfh = preprocess_point_cloud(target, voxel_size)
#     result_ransac = execute_global_registration(source_down, target_down,
#                                                 source_fpfh, target_fpfh,
#                                                 voxel_size)
#     return  o_to_tri(tri_to_o(source_mesh).transform(result_ransac))

In [259]:
import trimesh
import open3d as o3d

import copy


def draw_registration_result(source, target, transformation):
    source_temp = copy.deepcopy(source)
    target_temp = copy.deepcopy(target)
    source_temp.paint_uniform_color([1, 0.706, 0])
    target_temp.paint_uniform_color([0, 0.651, 0.929])
    source_temp.transform(transformation)
    o3d.visualization.draw_geometries([source_temp, target_temp])


def tri_to_o(trimesh_mesh: trimesh.Trimesh) -> o3d.geometry.TriangleMesh:
    vertices = np.asarray(trimesh_mesh.vertices)
    triangles = np.asarray(trimesh_mesh.faces)

    o3d_mesh = o3d.geometry.TriangleMesh()
    o3d_mesh.vertices = o3d.utility.Vector3dVector(vertices)
    o3d_mesh.triangles = o3d.utility.Vector3iVector(triangles)

    return o3d_mesh


def o_to_tri(o3d_mesh):
    vertices = np.asarray(o3d_mesh.vertices)
    faces = np.asarray(o3d_mesh.triangles)

    return trimesh.Trimesh(vertices=vertices, faces=faces)


def preprocess_point_cloud(pcd, voxel_size):
    print(":: Downsample with a voxel size %.3f." % voxel_size)
    pcd_down = pcd.voxel_down_sample(voxel_size)

    radius_normal = voxel_size * 2
    print(":: Estimate normal with search radius %.3f." % radius_normal)
    pcd_down.estimate_normals(
        o3d.geometry.KDTreeSearchParamHybrid(radius=radius_normal, max_nn=30)
    )

    radius_feature = voxel_size * 5
    print(":: Compute FPFH feature with search radius %.3f." % radius_feature)
    pcd_fpfh = o3d.pipelines.registration.compute_fpfh_feature(
        pcd_down,
        o3d.geometry.KDTreeSearchParamHybrid(radius=radius_feature, max_nn=100),
    )
    return pcd_down, pcd_fpfh


def execute_global_registration(
    source_down, target_down, source_fpfh, target_fpfh, voxel_size
):
    distance_threshold = voxel_size * 1.5
    result = o3d.pipelines.registration.registration_ransac_based_on_feature_matching(
        source_down,
        target_down,
        source_fpfh,
        target_fpfh,
        True,
        distance_threshold,
        o3d.pipelines.registration.TransformationEstimationPointToPoint(False),
        3,
        [
            o3d.pipelines.registration.CorrespondenceCheckerBasedOnEdgeLength(0.9),
            o3d.pipelines.registration.CorrespondenceCheckerBasedOnDistance(
                distance_threshold
            ),
        ],
        o3d.pipelines.registration.RANSACConvergenceCriteria(100000, 0.999),
    )
    return result


def align_f(source_mesh, target_mesh):
    voxel_size = 0.5

    # Convert to Open3D triangle meshes and sample point clouds
    target_pcd = tri_to_o(target_mesh).sample_points_uniformly(10000)
    source_pcd = tri_to_o(source_mesh).sample_points_uniformly(10000)

    # target_pcd = tri_to_o(target_mesh).sample_points_poisson_disk(10000)
    # source_pcd = tri_to_o(source_mesh).sample_points_poisson_disk(10000)
    # Preprocess point clouds
    source_down, source_fpfh = preprocess_point_cloud(source_pcd, voxel_size)
    target_down, target_fpfh = preprocess_point_cloud(target_pcd, voxel_size)

    # Register point clouds
    result_ransac = execute_global_registration(
        source_down, target_down, source_fpfh, target_fpfh, voxel_size
    )

    # Transform original Open3D mesh and convert back to trimesh
    source_o3d = tri_to_o(source_mesh)
    source_o3d.transform(result_ransac.transformation)

    return o_to_tri(source_o3d)

## Metrics

In [ ]:
def get_pca_axes(mesh: trimesh.Trimesh, n_components: int = 3):
    pca = PCA(n_components=n_components)
    pca.fit(mesh.vertices)
    return pca.components_  # (3, 3), строки — оси


def best_pca_alignment_score(axes1, axes2):
    """
    Ищет лучшую перестановку и отражения осей для максимального совпадения.
    """
    best_score = 0.0
    for perm in permutations(range(3)):
        permuted_axes2 = axes2[list(perm)]
        cosines = np.abs(np.sum(axes1 * permuted_axes2, axis=1))  # cosine similarity
        score = np.mean(cosines)
        best_score = max(best_score, score)
    return best_score


def orientation_similarity_pca_invariant(
    mesh1: trimesh.Trimesh, mesh2: trimesh.Trimesh
):
    axes1 = get_pca_axes(mesh1)  # (3, 3)
    axes2 = get_pca_axes(mesh2)  # (3, 3)
    return best_pca_alignment_score(axes1, axes2)


def orientation_similarity_faces(mesh1: trimesh.Trimesh, mesh2: trimesh.Trimesh):
    # Приводим к одинаковому количеству граней (если необходимо)
    if len(mesh1.face_normals) != len(mesh2.face_normals):
        return 0

    # Нормали граней
    n1 = mesh1.face_normals
    n2 = mesh2.face_normals

    # Косинусное сходство
    dot = np.abs(np.sum(n1 * n2, axis=1))
    score = np.mean(dot)

    return score  # 0..1, где 1 - идеальное совпадение ориентаций


def orientation_similarity_vertices(mesh1: trimesh.Trimesh, mesh2: trimesh.Trimesh):
    if mesh1.vertices.shape != mesh2.vertices.shape:
        return 0

    # Center the meshes at the origin
    v1 = mesh1.vertices - mesh1.vertices.mean(axis=0)
    v2 = mesh2.vertices - mesh2.vertices.mean(axis=0)

    # Normalize vertex vectors (direction only)
    v1_norm = v1 / np.linalg.norm(v1, axis=1, keepdims=True)
    v2_norm = v2 / np.linalg.norm(v2, axis=1, keepdims=True)

    # Cosine similarity per vertex
    cosines = np.sum(v1_norm * v2_norm, axis=1)  # dot products
    cosines = np.clip(cosines, -1.0, 1.0)  # numerical safety

    # Convert to absolute cosine similarity (no sign invariant)
    score = np.mean(cosines)

    # Normalize from [-1, 1] to [0, 1]
    normalized_score = (score + 1) / 2
    return normalized_score

## Visualize

In [245]:
def center_mesh(mesh: trimesh.Trimesh) -> trimesh.Trimesh:
    # Get the centroid of the mesh
    centroid = mesh.centroid

    # Create a translation matrix
    T = np.eye(4)
    T[:3, 3] = -centroid  # translate by negative centroid

    # Apply transformation
    centered = mesh.copy()
    centered.apply_transform(T)
    return centered


def transform(obj: trimesh.Trimesh) -> trimesh.Trimesh:
    """Normalizes a mesh to be centered and fit within a unit cube."""
    center = obj.bounds.mean(axis=0)
    obj.apply_translation(-center)
    scale = obj.extents.max()
    if scale > 1e-7:
        # if scale > 1:
        obj.apply_scale(1.0 / scale)
    return center_mesh(obj)


def plot_mesh_comparison_scene(
    meshes: list[Optional[trimesh.Trimesh]],
    colors: Optional[list[Optional[np.ndarray]]] = None,
    align: Optional[bool] = False,
):
    """
    Plot valid meshes side by side using trimesh's Scene system.

    Parameters:
        meshes: List of trimesh.Trimesh objects (some may be None or invalid).
        colors: Optional list of face colors (same length as meshes).
        align: Whether to align meshes to the first valid one (default: False).
    """
    scene = trimesh.Scene()
    valid_meshes = []
    valid_colors = []

    # Filter out None or empty/broken meshes
    for mesh, color in zip(meshes, colors or [None] * len(meshes)):
        if mesh is None or not isinstance(mesh, trimesh.Trimesh) or mesh.is_empty:
            print("Warning: Skipping empty or invalid mesh.")
            continue
        valid_meshes.append(mesh)
        valid_colors.append(color)

    if not valid_meshes:
        raise ValueError("No valid meshes to display.")

    valid_meshes = [transform(m) for m in valid_meshes]
    # Compute offset based on valid meshes only
    offset = max(m.extents[0] for m in valid_meshes) * 1.2

    # Center the baseline mesh (first one)
    baseline = valid_meshes[0]

    for m in valid_meshes[1:]:
        print(
            orientation_similarity_pca_invariant(baseline, m),
            orientation_similarity_faces(baseline, m),
            orientation_similarity_vertices(baseline, m),
        )

    for idx, (mesh, color) in enumerate(zip(valid_meshes, valid_colors)):
        mesh.visual.face_colors = None if color is None else color
        if idx > 0 and align:
            # mesh = align_mesh(mesh, baseline)
            # mesh = align_meshes(mesh, baseline)
            # mesh = transform(align_rot(mesh, baseline))
            # mesh = transform(align_rot2(mesh, baseline))
            mesh = transform(align_f(mesh, baseline))
        scene.add_geometry(
            mesh,
            transform=trimesh.transformations.translation_matrix([offset * idx, 0, 0]),
        )

    return scene.show()

## Experiments

### Box

In [ ]:
def get_box() -> trimesh.Trimesh:
    # Box parameters
    width = 100  # X-axis
    depth = 150  # Y-axis
    bottom_thickness = 10
    wall_height = 40

    # Wall thicknesses
    t_left = 15
    t_right = 15
    t_front = 30
    t_back = 30

    meshes = []

    # Bottom plate
    bottom = trimesh.creation.box(extents=(width, depth, bottom_thickness))
    bottom.apply_translation([width / 2, depth / 2, bottom_thickness / 2])
    meshes.append(bottom)

    # Left wall
    left_wall = trimesh.creation.box(extents=(t_left, depth, wall_height))
    left_wall.apply_translation(
        [t_left / 2, depth / 2, bottom_thickness + wall_height / 2]
    )
    meshes.append(left_wall)

    # Right wall
    right_wall = trimesh.creation.box(extents=(t_right, depth, wall_height))
    right_wall.apply_translation(
        [width - t_right / 2, depth / 2, bottom_thickness + wall_height / 2]
    )
    meshes.append(right_wall)

    # Front wall
    front_wall = trimesh.creation.box(
        extents=(width - t_left - t_right, t_front, wall_height)
    )
    front_wall.apply_translation(
        [
            t_left + (width - t_left - t_right) / 2,
            t_front / 2,
            bottom_thickness + wall_height / 2,
        ]
    )
    meshes.append(front_wall)

    # Back wall
    back_wall = trimesh.creation.box(
        extents=(width - t_left - t_right, t_back, wall_height)
    )
    back_wall.apply_translation(
        [
            t_left + (width - t_left - t_right) / 2,
            depth - t_back / 2,
            bottom_thickness + wall_height / 2,
        ]
    )
    meshes.append(back_wall)

    # Combine into one mesh
    box = trimesh.util.concatenate(meshes)
    return box


box = get_box()

In [ ]:
plot_mesh_comparison_scene(
    [
        box,
        box,
        *[
            box.copy().apply_transform(
                trimesh.transformations.rotation_matrix(angle, d, [0, 0, 0])
            )
            for angle in [3.14, 3.14 / 2, 3.14 / 4]
            for d in [[1, 0, 0], [0, 1, 0], [0, 0, 1]]
        ],
    ],
    align=True,
)

1.0000000000000002 1.0 1.0
0.9999991544850264 0.9999991544850263 0.25129316823066083
0.9999991544850264 0.9999991544850262 0.6833458870541667
0.9999991544850264 0.9999991544850263 0.06536221298763306
0.999999788621223 0.33386421780715553 0.6259444545374802
0.999999788621223 0.3338642178071556 0.84179892327015
0.9999997886212233 0.3338642178071556 0.5330529489031032
0.8049255127781333 0.8049255127781331 0.8904597295713615
0.8049255127781333 0.804925512778133 0.9536716165892909
0.8049255127781331 0.804925512778133 0.8632569230065472


### Prism

In [ ]:
def get_prism():
    # Parameters
    n_sides = 10  # Decagon
    side_length = 20.0  # Length of one side (mm)
    height = 200.0  # Extrusion height (mm)

    # Compute the radius of the circumcircle
    angle = np.pi / n_sides
    radius = side_length / (2 * np.sin(angle))

    # Generate decagon vertices (CCW order)
    vertices_2d = [
        (
            radius * np.cos(2 * np.pi * i / n_sides),
            radius * np.sin(2 * np.pi * i / n_sides),
        )
        for i in range(n_sides)
    ]

    # Create shapely polygon
    base_polygon = Polygon(vertices_2d)

    # Extrude into a prism
    prism = trimesh.creation.extrude_polygon(base_polygon, height=height)
    return prism


prism = get_prism()

In [ ]:
plot_mesh_comparison_scene(
    [
        prism,
        prism,
        *[
            prism.copy().apply_transform(
                trimesh.transformations.rotation_matrix(angle, d, [0, 0, 0])
            )
            for angle in [3.14 / 2, 3.14 / 4]
            for d in [[1, 0, 0], [0, 1, 0], [0, 0, 1]]
        ],
    ],
    align=True,
)

0.9999999999999997 1.0 0.9999999999999999
0.999999788621223 0.2783529026244184 0.5240778827320305
0.999999788621223 0.2783529026244185 0.5240778827320305
0.9999999999999999 0.44488684817262975 0.9526405612466723
0.8049255127781331 0.7886693055096443 0.8606286203722993
0.8049255127781331 0.7886693055096443 0.8606286203722993
0.9999999999999999 0.837437927315111 0.9861310284226014


### Real Box

In [260]:
def predicted_box():
    base = cq.Workplane("XY").box(150, 100, 10)
    walls = (
        cq.Workplane("XY")
        .rect(150, 100)
        .extrude(40)
        .faces(">Z")
        .workplane()
        .rect(150 - 30 * 2, 100 - 15 * 2)
        .cutThruAll()
    )
    return base.union(walls)


pred_box = cq_to_trimesh(predicted_box())

plot_mesh_comparison_scene(
    [box, pred_box],
    align=True,
)

0.9999999999999999 0 0
:: Downsample with a voxel size 0.500.
:: Estimate normal with search radius 1.000.
:: Compute FPFH feature with search radius 2.500.
:: Downsample with a voxel size 0.500.
:: Estimate normal with search radius 1.000.
:: Compute FPFH feature with search radius 2.500.


In [ ]:
plot_vertices(box)

# Vertices: 40


In [ ]:
plot_vertices(pred_box)

# Vertices: 16
